In [118]:
from datasets import load_dataset
from transformers import AutoTokenizer, AutoModelForTokenClassification
from sklearn.metrics import classification_report
import numpy as np
import pandas as pd
import torch

In [119]:
#check the avaialbility of cuda
import torch
torch.cuda.is_available()

False

# 0. Summary

# 1. Data processing

### a. mounting, aggregating

- There are 1008 preqs_pairs, pairs of concepts with prerequisite labels

In [120]:
# from google.colab import drive
# drive.mount('/content/drive')
# !ls '/content/drive/MyDrive/thesis/'

import json, csv
from datasets import Dataset, DatasetDict

# File path
preqs_path = './data/cs_preqs.csv'
text_path = './data/cs_courses.csv'
concept_vocab_path = './data/concept_vocab.pkl'
bow_feature_text_path = './data/bow_feature.txt'
preqs_idx_path = './data/cs_preqs_index.txt'

In [121]:
import pickle

# Open the file
with open(concept_vocab_path, 'rb') as file:
    concept_vocab = pickle.load(file)

print(concept_vocab)

# # Replace underscores with spaces
# concept_vocab = {key: value.replace('_', ' ') for key, value in concept_vocab.items()}

# print(concept_vocab)

{24580: 'Lock_(computer_science)', 47129: 'Volume_rendering', 18459: 'Graphical_model', 24606: 'Logic', 18500: 'Graph_(mathematics)', 16454: 'File_system', 47176: 'Vulnerability_(computing)', 6217: 'Cloud_computing', 28748: 'Nonlinear_system', 36942: 'Robot', 34896: 'Quantum_computer', 34898: 'Quantum_cryptography', 34907: 'Quantum_mechanics', 6239: 'Cluster_analysis', 24695: 'Logic_programming', 36989: 'Robotics', 26757: 'ML_(programming_language)', 47238: 'Wavelet', 24715: 'Very_long_instruction_word', 8333: 'Concurrency_control', 26774: 'Mobile_device', 34969: 'Query_language', 30887: 'Perl', 28840: 'NP-complete', 34985: 'Query_optimization', 8364: 'Concurrency_(computer_science)', 42014: 'Symmetric_multiprocessing', 35007: 'Question_answering', 16580: 'Finite_difference', 47305: 'Web_browser', 16587: 'Finite_element_method', 16595: 'Finite-state_machine', 30933: 'Personal_computer', 8408: 'Conditional_probability', 26842: 'Model_checking', 22752: 'Java_(programming_language)', 4734

### b. merging
- Comments
  - There are 345 concepts in the concept vocab
- Description
  - bow_feature.txt: bow_feature.txt ( # 1-gram | idx of 1-gram 1: frequency | idx of 1-gram 2: frequency | ....)
  - concept_covab: concept | idx
- Target
  - target 1: text_corpus | concept1 | concept2 | … | conceptn
  - target 2: idx 1 | idx 2 | concept1 | concept2 | aggr_corpus1 | aggr_corpus2


#### Target 1: text | concepts
- Algo for the Target 1
  - From ``bow_feature.txt`` creating a dicttionary type of file, key = int, values, list of vocab {1: [ a list of word_idx]}. Then, I would have a df:  text_idx | word_idxes.
  - Filtering uneccessary word_indexes, keep the word that is in ``concepts_vocab``. text_idx | concepts_vocab_idx.
  - Replace text_idx =  text, concept_vocab_idx = concepts, . Done target 2: text | concepts

In [122]:
# Creating a nested list of the vocabulary from each copra corresponding to each line.
# then remainning the extracted concepts in each copra

file = open(bow_feature_text_path, "r") # Open the file
bow_feature = file.read()

# Splitting the text into lines
lines = bow_feature.split('\n')

bow_feature = [] # the vocabulary from each copra corresponding to each line
extracted_concepts = [] # the extracted concepts from each copra
extracted_concepts_idx = [] # the idxes of extracted concepts from each copra
for element in lines:
  bow_per_line = []
  concept_per_line = []
  concept_per_line_idx = []
    # Splitting each line by spaces
  parts = element.split()

  for part in parts:
        # Check if the part is a key (just a number) or a value (number:1,2,3,..)
        if ':' not in part:
            # If we encounter a new key, we save the previous key and its values to the dictionary
          continue
        else:
          word_idx = int(part.split(':')[0])
            # Add the value (before the colon) to the current values
          bow_per_line.append(word_idx)

          # Filtering the words that are not in the concept vocab
          if word_idx in concept_vocab.keys():
            concept_per_line.append(concept_vocab[word_idx])
            concept_per_line_idx.append(word_idx)
          else:
             continue
  extracted_concepts.append(concept_per_line)
  extracted_concepts_idx.append(concept_per_line_idx)
  bow_feature.append(bow_per_line)
print(bow_feature)
print(extracted_concepts)
print(extracted_concepts_idx)
# print(extracted_concepts[653])
# print(bow_feature[653]) # the last copra, 654th course's description.
#creating a dataframe of course_id, text from text_dicts and extracted_concepts

[[445, 450, 451, 531, 532, 533, 1197, 1198, 1199, 3637, 3657, 3662, 3663, 3664, 3823, 3824, 3825, 5401, 5402, 5406, 5441, 5452, 5459, 6149, 6150, 6151, 6640, 6664, 6666, 6749, 6783, 6784, 7241, 7242, 7243, 7596, 7796, 7835, 7847, 7863, 7864, 8312, 8313, 8314, 9440, 9530, 9534, 9782, 9783, 9793, 9805, 9806, 11272, 11273, 11274, 11517, 11520, 11521, 12030, 12048, 12049, 14894, 15840, 15841, 15842, 16166, 16173, 16174, 18996, 19003, 19004, 20048, 20049, 20050, 20063, 20319, 20320, 20389, 20630, 20631, 20673, 20676, 20677, 21241, 21246, 21247, 21876, 21877, 21878, 23998, 24003, 24004, 24227, 24230, 24231, 25066, 25075, 25076, 25976, 25983, 25984, 26099, 26100, 26101, 27689, 27699, 27700, 29629, 29630, 29631, 29644, 29646, 31769, 31807, 31808, 32073, 32080, 32081, 32403, 32404, 32860, 32879, 32880, 33283, 33284, 33285, 33286, 33287, 34118, 34176, 34177, 34180, 34181, 35437, 35440, 35442, 35875, 35912, 35913, 36227, 36228, 36229, 36446, 36462, 36463, 36504, 36506, 36567, 36568, 37571, 37666,

In [133]:
print(extracted_concepts[653])
print(bow_feature[653]) # the last copra, 654th course's description.

['Communication', 'Variable_(computer_science)']
[3524, 3540, 3541, 3823, 6640, 6719, 6720, 6729, 6731, 10028, 10039, 10040, 12702, 12707, 13813, 13826, 13827, 15947, 15950, 15951, 21211, 21212, 21213, 23988, 23993, 23994, 28869, 28878, 28879, 29629, 29634, 29638, 29644, 29645, 32073, 32078, 32079, 32091, 32092, 34585, 34604, 34605, 35164, 35169, 35170, 36836, 36837, 36838, 38720, 38723, 38724, 39180, 39228, 39229, 41117, 41192, 41194, 42843, 42846, 42847, 43007, 43046, 43047, 46162, 46175, 46176, 46635, 46636, 46637, 47641, 47642, 47643]


In [123]:
#creating a dataframe of course_id, text from text_dicts and extracted_concepts
#importing the copra | course_id
import pandas as pd
# draft
def text_to_dict(file_path):
    data_dicts = []
    with open(file_path, newline='', encoding='utf-8') as csvfile:
        reader = csv.reader(csvfile)
        for idx, row in enumerate(reader):
            # Assuming each row has two course codes
            code, description = row
            data_dicts.append({
                'course_code': code,
                'text': description,
            })
    return data_dicts

text_dicts = text_to_dict(text_path)

# Print the first dictionary to verify the output
df = pd.DataFrame(text_dicts)
df['extracted_concepts'] = extracted_concepts
df['extracted_concepts_idx'] = extracted_concepts_idx
df['bow_feature'] = bow_feature
df.head(2)

course_code                                               text  \
0  cmu_15-221  Technical Communication for Computer Scientist...   
1   mit_6.641  Electromagnetic Fields, Forces, and Motion. El...   

                                  extracted_concepts   extracted_concepts_idx  \
0  [Abstraction_(computer_science), Communication...  [531, 6640, 7596, 7796]   
1                           [Boundary_value_problem]                   [4938]   

                                         bow_feature  
0  [445, 450, 451, 531, 532, 533, 1197, 1198, 119...  
1  [2602, 2806, 2807, 2841, 2853, 2854, 4934, 493...

#### Target 2: concepts_pairs | text
  - Merging ``preqs_idx`` | ``preqs`` |. We have 4 first columns in target 1
  - Creating an empty aggr_corpus1 column. Row by Row, Compare each element in the idx1 columm; and each element in the concepts_vocab_idx column of ``text_idx | concepts_vocab_idx`` table. Then aggretate those corpus and assign them to the **aggr_corpus1** column. Same for **aggr_corpus2** column.

In [144]:
#indexes pairs of 2 concepts
preqs_idx_path = './data/cs_preqs_index.txt'
preqs_index = []
with open(preqs_idx_path, "r") as file:
    preqs_index = file.read().split('\n')

# context pairs of 2 concepts
preqs = pd.read_csv(preqs_path, header=None)

# Split the string on comma
for i in range(len(preqs_index)):
    preqs_index[i] = preqs_index[i].split(',')

# Create a DataFrame with two columns
preqs_index = pd.DataFrame(preqs_index, columns=['Column1', 'Column2'])

# merge preqs concepts and their indexes into a dataframe
preqs['idx1'] = preqs_index['Column1']
preqs['idx2'] = preqs_index['Column2']
preqs.columns = ['concept1', 'concept2', 'idx1', 'idx2']

# Remove underscores in preqs dataframe
preqs['concept1'] = preqs['concept1'].str.replace('_', ' ')
preqs['concept2'] = preqs['concept2'].str.replace('_', ' ')

preqs.head(2)


concept1          concept2   idx1   idx2
0                            Random graph       Mathematics  35081  25633
1  Knowledge representation and reasoning  Algorithm design  22997   1296

### importing splitted data


In [125]:
import pandas as pd

# Read the data from the "data-base" folder
dev = pd.read_csv('./data/data-base/data_dev.csv')
test = pd.read_csv('./data/data-base/data_test.csv')
train = pd.read_csv('./data/data-base/data_train.csv')

In [126]:
train.head(2)

concept1             concept2  label
0  Concurrency (computer science)             Integral      0
1                         Shading  Formal verification      0

In [127]:
df['extracted_concepts'] = df['extracted_concepts'].apply(lambda x: [concept.replace('_', ' ') for concept in x])
df.head(2)

course_code                                               text  \
0  cmu_15-221  Technical Communication for Computer Scientist...   
1   mit_6.641  Electromagnetic Fields, Forces, and Motion. El...   

                                  extracted_concepts   extracted_concepts_idx  \
0  [Abstraction (computer science), Communication...  [531, 6640, 7596, 7796]   
1                           [Boundary value problem]                   [4938]   

                                         bow_feature  
0  [445, 450, 451, 531, 532, 533, 1197, 1198, 119...  
1  [2602, 2806, 2807, 2841, 2853, 2854, 4934, 493...

In [ ]:
train['']

In [143]:
train['concept1_idx'] = None
for idx, row in train.iterrows():
    for value, key in concept_vocab.items():
        if row['concept1'] == value.replace('_', ' '):
            row['concept1_idx'] = key
            break
train['concept2_idx'] = None
# for idx, row in train.iterrows():
#     for value, key in concept_vocab.items():
#         if row['concept2'] == value.replace('_', ' '):
#             row['concept2_idx'] = key
#             break
# train.head(5)

7596
8364
38728
44936
29007
45895
47095
19040
34907
47095
7596
15929
47305
18459
35127
468
17940
30215
7300
6527
21848
24715
17354
3495
13034
36989
35381
44217
26052
47095
24872
30375
10581
37499
13956
41736
7114
27513
17354
7879
18357
47238
26052
47095
3772
11164
13235
13244
21643
10217
13614
37225
13614
29919
7615
28560
1288
2331


18032
35104
3043
26757
7786
4631
14270
1288
7442
47095
35954
16245
45604
30244
3388
3495
8373
11864
33703
28058
45394
4679
24314
8333
26757
5270
16595
35628
18459
43915
21534
37791
47095
35972
30375
27835
26842
18459
18886
39445
39418
29038
38728
27109
43915
47095
5270
26774
7796
35972
17122
27109
27109
35127
8823
8004
13403
45580
26842
17695
8408
1296
12743
39336
37357
7920
47095
25404
33703
28280
46635
3974
30933
47095
25368
15929
16580
40768
6903
24833
30375
18704
33307
25659
41789
30403
6527
30403
3043
1296
36942
22863
42014
8466
5216
47095
43834
38484
35007
19742
47095
6640
35628
16454
25125
7300
10709
21643
4938
40169
47353
34985
42025
18886
47095
10864
3388
47095
21128
3974
30244
29260
24695
18357
24606
38285
34699
13244
22774
19742
47095
24833
43834
35146
39418
31584
11864
24833
40768
20746
18886
40507
10217
35638
45922
47095
2331
47095
43834
17354
3495
7879
13403
39991
34793
10564
8373
22741
2331
10217
16595
39587
27608
32523
25605
47095
24454
46881
22752
39478
8004
29007
2438

In [ ]:
train['corpus1'] = None
for index, row in train.iterrows():
    for idx,roww in df.iterrows():
        print(row['concept1_idx'], roww['extracted_concepts_idx'])
        if row['concept1_idx'] in roww['extracted_concepts_idx']:
            train.at[index, 'corpus1'] = roww['text']
            break
train.head(2)

253.0 [531, 6640, 7596, 7796]
253.0 [4938]
253.0 [4938, 29705]
253.0 [3495]
253.0 [7596, 7796]
253.0 [7104, 7596, 7796, 11018]
253.0 [10564, 33314, 42622, 45895]
253.0 []
253.0 [6640, 8004, 21820, 22774, 38636]
253.0 [7104, 7596, 7796, 16623, 17695]
253.0 [3586, 11100, 27410, 33803, 38636]
253.0 []
253.0 [6640, 11100, 21518, 26052, 37962, 42025, 42622]
253.0 []
253.0 [7596, 10564, 37225, 37499, 38870]
253.0 [3043, 21897, 29705, 31587]
253.0 [7318, 11352, 38285, 38306]
253.0 []
253.0 [6640]
253.0 [7596]
253.0 [8333, 10564, 10900, 34985]
253.0 [1219, 3495, 5270, 7596, 7796, 7879, 8004, 10564, 18500, 24314, 25368, 32523, 32567, 35081, 35099, 35109, 35127, 45580, 47342]
253.0 [16454, 20746, 27949, 29260, 31955, 42025, 46881]
253.0 [13614, 22129, 24359, 28839]
253.0 [7596, 7677, 18393, 21643, 21897, 35231, 38728, 47095]
253.0 [8004, 10564, 22129, 30887]
253.0 [7596, 8823, 28053, 28058, 30375, 35007]
253.0 [7104, 8004, 10564, 35146, 35638, 39403]
253.0 [20868, 25592, 27109, 35381]
253.0 []
2

concept1    concept2  label  concept1_idx  concept2_idx corpus1
9        Computer  Arithmetic      1         253.0         236.0    None
18  Combinatorics     Algebra      1          66.0         214.0    None